In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import pandas as pd
import pycountry

# Download monitor measurements

In [ ]:
import download_measurements

In [ ]:
import multiprocessing
from joblib import Parallel, delayed

In [ ]:
# Get all raw monitor data + Oxford stringency data

In [ ]:
num_cores = 12

## Japan

In [ ]:
# Japan
# Get the list of all possible combinations of year, month, province based on
# the data structure
lst_months_jp = []
for year in [2016, 2017]:
    for prov in range(1,48):
        lst_months_jp.append((year, 0, prov))
#for month in range(5,13):
#    for prov in range(1,48):
#        lst_months_jp.append((2019, month, prov))
#for month in range(1,7):
#    for prov in range(1,48):
#        lst_months_jp.append((2020, month, prov))

In [ ]:
res = Parallel(n_jobs=num_cores)(delayed(download_measurements.jp_monitor_data)(year, month, prov) for (year, month, prov) in lst_months_jp)

In [ ]:
# Sequential
download_measurements.jp_monitor_data(year)

## Europe

In [ ]:
import os, pycountry

In [ ]:
pycountry.countries.get(alpha_2='MK').name

In [ ]:
# Europe
short_countries = ['BG','IS','DK','CZ','SI','AD','GI','GR','CH',
                   'HU','RO','LU','ME','LV','LT','CY','RS','MK',
                   'TR','PT','MT','SE','HR','NL','IE','GE',
                   'NO','BA','BE','SK','PL','FI','EE','AT','AL',
                   'FR', 'DE', 'GB', 'IT', 'ES']
# long_countries = [pycountry.countries.get(alpha_2=c).name for c in short_countries]
lst_eu = []
for year in range(2016, 2021):
    for country in short_countries:
        lst_eu.append((year, country))
        download_measurements.eu_monitor_data(year, country)

In [ ]:
path = '/net/fs03/d1/gchossie/2020_aq/monitor_data/raw_data/europe/'
for year in range(2016, 2021):
    for country in short_countries:
        for sp in ['NO2', 'PM2.5', 'O3']:
            if not os.path.exists(path + f'{country}_raw_{year}_{sp}.feather'):
                print(country, year, sp)

In [ ]:
year, country

In [ ]:
# Parallel download
num_cores = 24
Parallel(n_jobs=num_cores)(delayed(download_measurements.eu_monitor_data)(
    year, country) for (year, country) in lst_eu)

## US

In [ ]:
# US
Parallel(n_jobs=5)(delayed(download_measurements.us_monitor_data)(year)
                   for year in range(2016, 2021))

In [ ]:
download_measurements.us_monitor_data(year)

## China

In [ ]:
# China
Parallel(n_jobs=4)(delayed(download_measurements.ch_monitor_data)(year)
                   for year in range(2016, 2020))

In [ ]:
download_measurements.ch_monitor_data(year)

## South Korea

In [ ]:
# South Korea
download_measurements.kr_monitor_data(year)

In [ ]:
Parallel(n_jobs=num_cores)(delayed(download_measurements.kr_monitor_data)(year) for year in range(2016, 2021))

In [ ]:
download_measurements.kr_monitor_data_recent(year)

In [ ]:
# Need to scrape data from the website for April and May 2020
if year == 2020:
    download_measurements.kr_monitor_data_recent(year)

In [ ]:
# Get Oxford strigency index
download_measurements.get_oxford_strigency()

# Get information on monitors

In [ ]:
%load_ext autoreload
%autoreload 2

In [ ]:
import get_monitor_info

Download the monitor info the AQ agencies

In [ ]:
get_monitor_info.us_monitor_utility()

In [ ]:
get_monitor_info.jp_monitor_utility()

In [ ]:
get_monitor_info.kr_monitor_utility()
get_monitor_info.geocode_kr_monitor_locations()

In [ ]:
get_monitor_info.eu_monitor_utility()

NB: the Chinese monitor data is already provided alongside the code.

Gets a dictionaries of dataframes (1 per species) with a unique ID, 
the country, region, and population. Population of grid cells with more
than 1 monitor is split equally between monitors. The ID column of these df
are used to built the regional time series of measurements

In [ ]:
monitors = get_monitor_info.merge_all_monitor_data()

In [ ]:
!ls -larth raw_data/europe

In [ ]:
eu_monitor_utility()

# Process raw measurements

In [ ]:
import process_measurements

In [ ]:
year = 2020; sp = 'O3'

In [ ]:
year = 2020
df = process_measurements.initialize_df(year, sp)
%prun df = process_measurements.add_kr_measurements(df, year, sp)

In [ ]:
df.dropna(axis=0, how='all')

In [ ]:
import pickle
import numpy as np

In [ ]:
path = '/net/fs03/d1/gchossie/2020_aq/monitor_data/raw_data/'
out = pd.DataFrame()
for year in range(2016,2021):
    with open(path + f'O3_{year}_all_measurements.pkl', 'rb') as f:
        tst = pickle.load(f)
    out = pd.concat([out, tst], axis=1)

In [ ]:
out.values[out.values == -9999] = np.nan

In [ ]:
out.dropna(axis=0, how='all')#thresh=np.floor(0.9*out.shape[1]))

In [ ]:
with open(path + f'O3_all_measurements.pkl', 'wb') as f:
    pickle.dump(out, f)

# Create time-series for testing

In [3]:
datadir = '/net/fs03/d1/gchossie/2020_aq/monitor_data/raw_data/'

In [28]:
import test_significance

In [36]:
(sp, region) = ('NO2', 'Massachusetts')

In [37]:
test_significance.create_ts(sp,region)

/home/gchossie/anaconda3/envs/freight_us/lib/python3.8/site-packages/pandas/core/indexing.py:1048: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[item_labels[indexer[info_axis]]] = value


date      value
0    2016-01-01  14.638693
1    2016-01-02  14.809497
2    2016-01-03  13.901877
3    2016-01-04  12.628944
4    2016-01-05  13.541568
...         ...        ...
1634 2020-06-22  17.984141
1635 2020-06-23  24.221653
1636 2020-06-24  23.760187
1637 2020-06-25  27.433644
1638 2020-06-26  31.803980

[1639 rows x 2 columns]

# Interpolate monitor data to create prediction time series

In [32]:
sp = 'O3'

In [38]:
PATH = '/net/fs03/d1/gchossie/2020_aq/monitor_data/raw_data/'
vals = pd.read_pickle(PATH + f'{sp}_all_measurements.pkl')
monitors = pd.read_feather(PATH + f'{sp}_monitor_locations.feather')

In [43]:
vals = vals.reset_index().rename(columns={'index': 'Identifier'}); vals

Identifier 2016-01-01 00:00:00 2016-01-02 00:00:00  \
0          STA_ES1964A                 NaN                 NaN   
1       STA.DE_DENW181                 NaN                 NaN   
2          STA-BETR804                 NaN                 NaN   
3             12225080              33.913             33.3043   
4          STA.IT0912A             9.89492             8.67099   
...                ...                 ...                 ...   
10774        420750100                  60                  56   
10775            1162A               47.25             27.5417   
10776   STA.DE_DERP063                 NaN                 NaN   
10777            1390A             63.3333              38.125   
10778  Station_GB0729A             60.2015             75.5622   

      2016-01-03 00:00:00 2016-01-04 00:00:00 2016-01-05 00:00:00  \
0                     NaN                 NaN                 NaN   
1                     NaN                 NaN                 NaN   
2                     NaN                 NaN                 NaN   
3                 42.6957             60.9565             51.1304   
4                  20.101             15.0076             7.79559   
...                   ...                 ...                 ...   
10774                  54                  62                  56   
10775             12.2917               21.75               77.25   
10776                 NaN                 NaN                 NaN   
10777             24.7917             24.7273             11.3636   
10778             52.8923             65.4714             69.4628   

      2016-01-06 00:00:00 2016-01-07 00:00:00 2016-01-08 00:00:00  \
0                     NaN                 NaN                 NaN   
1                     NaN                 NaN                 NaN   
2                     NaN                 NaN                 NaN   
3                 39.4783             15.9091             24.4348   
4                     NaN                 NaN             1.13434   
...                   ...                 ...                 ...   
10774                  40                   8                   0   
10775             49.9583             18.8333             38.3333   
10776                 NaN                 NaN                 NaN   
10777             33.5833             68.1667                  49   
10778             69.7393             70.2133             67.8309   

      2016-01-09 00:00:00  ... 2020-06-17 00:00:00 2020-06-18 00:00:00  \
0                     NaN  ...                 NaN                 NaN   
1                     NaN  ...                 NaN                 NaN   
2                     NaN  ...                 NaN                 NaN   
3                 39.5652  ...                 NaN                 NaN   
4                0.984657  ...             98.2324             90.1567   
...                   ...  ...                 ...                 ...   
10774                   0  ...                 NaN                 NaN   
10775                  41  ...             100.708              53.875   
10776                 NaN  ...                 NaN                 NaN   
10777                  45  ...              35.375             41.2917   
10778             45.9011  ...             77.9071             86.8628   

      2020-06-19 00:00:00 2020-06-20 00:00:00 2020-06-21 00:00:00  \
0                     NaN                 NaN                 NaN   
1                     NaN                 NaN                 NaN   
2                     NaN                 NaN                 NaN   
3                     NaN                 NaN                 NaN   
4                 103.934             111.554              104.84   
...                   ...                 ...                 ...   
10774                 NaN                 NaN                 NaN   
10775             101.783             102.708             76.9583   
10776                 NaN                 NaN      

In [45]:
pd.merge(vals, monitors[['Identifier', 'Latitude', 'Longitude']], on='Identifier').set_index('Identifier')

2016-01-01 00:00:00 2016-01-02 00:00:00 2016-01-03 00:00:00  \
Identifier                                                                    
STA_ES1964A                     NaN                 NaN                 NaN   
STA.DE_DENW181                  NaN                 NaN                 NaN   
STA-BETR804                     NaN                 NaN                 NaN   
12225080                     33.913             33.3043             42.6957   
STA.IT0912A                 9.89492             8.67099              20.101   
...                             ...                 ...                 ...   
STA-PT03075                     NaN                 NaN                 NaN   
1162A                         47.25             27.5417             12.2917   
STA.DE_DERP063                  NaN                 NaN                 NaN   
1390A                       63.3333              38.125             24.7917   
Station_GB0729A             60.2015             75.5622             52.8923   

                2016-01-04 00:00:00 2016-01-05 00:00:00 2016-01-06 00:00:00  \
Identifier                                                                    
STA_ES1964A                     NaN                 NaN                 NaN   
STA.DE_DENW181                  NaN                 NaN                 NaN   
STA-BETR804                     NaN                 NaN                 NaN   
12225080                    60.9565             51.1304             39.4783   
STA.IT0912A                 15.0076             7.79559                 NaN   
...                             ...                 ...                 ...   
STA-PT03075                     NaN                 NaN                 NaN   
1162A                         21.75               77.25             49.9583   
STA.DE_DERP063                  NaN                 NaN                 NaN   
1390A                       24.7273             11.3636             33.5833   
Station_GB0729A             65.4714             69.4628             69.7393   

                2016-01-07 00:00:00 2016-01-08 00:00:00 2016-01-09 00:00:00  \
Identifier                                                                    
STA_ES1964A                     NaN                 NaN                 NaN   
STA.DE_DENW181                  NaN                 NaN                 NaN   
STA-BETR804                     NaN                 NaN                 NaN   
12225080                    15.9091             24.4348             39.5652   
STA.IT0912A                     NaN             1.13434            0.984657   
...                             ...                 ...                 ...   
STA-PT03075                     NaN                 NaN                 NaN   
1162A                       18.8333             38.3333                  41   
STA.DE_DERP063                  NaN                 NaN                 NaN   
1390A                       68.1667                  49                  45   
Station_GB0729A             70.2133             67.8309             45.9011   

                2016-01-10 00:00:00  ... 2020-06-19 00:00:00  \
Identifier                           ...                       
STA_ES1964A                     NaN  ...                 NaN   
STA.DE_DENW181                  NaN  ...                 NaN   
STA-BETR804                     NaN  ...                 NaN   
12225080                    38.3478  ...                 NaN   
STA.IT0912A                 4.24015  ...             103.934   
...                             ...  ...                 ...   
STA-PT03075                     NaN  ...                 NaN   
1162A                        28.375  ...             101.783   
STA.DE_DERP063                  NaN  ...                 NaN   
1390A                       35.4583  ...             48.0833   
Station_GB0729A             65.9828  ...             86.6633   

                2020-06-20 00:00:00 2020-06-21 00:00:00 2020-06-22 00:00:00  \
Identifier          

In [47]:
import interpolate

In [48]:
%time interpolate.preprocess_raw_vals('NO2')

CPU times: user 4.28 s, sys: 1.04 s, total: 5.32 s
Wall time: 5.33 s


2016-01-01 00:00:00 2016-01-02 00:00:00 2016-01-03 00:00:00  \
Identifier                                                                    
12225080                     33.913             33.3043             42.6957   
STA.IT0912A                 9.89492             8.67099              20.101   
14215010                     53.913             47.6522             56.8696   
1368A                        76.625              67.125               39.75   
STA_PL0605A                     NaN                 NaN                 NaN   
...                             ...                 ...                 ...   
STA_PL0768A                     NaN                 NaN                 NaN   
22220010                    54.5217                  54             53.2727   
1162A                         47.25             27.5417             12.2917   
1390A                       63.3333              38.125             24.7917   
Station_GB0729A             60.2015             75.5622             52.8923   

                2016-01-04 00:00:00 2016-01-05 00:00:00 2016-01-06 00:00:00  \
Identifier                                                                    
12225080                    60.9565             51.1304             39.4783   
STA.IT0912A                 15.0076             7.79559                 NaN   
14215010                    49.2174             60.6957             36.0909   
1368A                         37.25                  46              70.625   
STA_PL0605A                     NaN                 NaN                 NaN   
...                             ...                 ...                 ...   
STA_PL0768A                     NaN                 NaN                 NaN   
22220010                     46.087             34.5217             30.5217   
1162A                         21.75               77.25             49.9583   
1390A                       24.7273             11.3636             33.5833   
Station_GB0729A             65.4714             69.4628             69.7393   

                2016-01-07 00:00:00 2016-01-08 00:00:00 2016-01-09 00:00:00  \
Identifier                                                                    
12225080                    15.9091             24.4348             39.5652   
STA.IT0912A                     NaN             1.13434            0.984657   
14215010                    19.7391             42.6087             40.8696   
1368A                       74.6667             72.7917             66.9583   
STA_PL0605A                     NaN                 NaN                 NaN   
...                             ...                 ...                 ...   
STA_PL0768A                     NaN                 NaN                 NaN   
22220010                    33.6522             60.9091             47.0435   
1162A                       18.8333             38.3333                  41   
1390A                       68.1667                  49                  45   
Station_GB0729A             70.2133             67.8309             45.9011   

                2016-01-10 00:00:00  ... 2020-06-19 00:00:00  \
Identifier                           ...                       
12225080                    38.3478  ...                 NaN   
STA.IT0912A                 4.24015  ...             103.934   
14215010                    20.8696  ...                 NaN   
1368A                         73.25  ...              32.375   
STA_PL0605A                     NaN  ...                 NaN   
...                             ...  ...                 ...   
STA_PL0768A                     NaN  ...              74.875   
22220010                    28.6957  ...                 NaN   
1162A                        28.375  ...             101.783   
1390A                       35.4583  ...             48.0833   
Station_GB0729A             65.9828  ...             86.6633   

                2020-06-20 00:00:00 2020-06-21 00:00:00 2020-06-22 00:00:00  \
Identifier          